# Data cleaning - image processing


In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from ast import literal_eval
import ast
import random
from skimage import io
from wordcloud import WordCloud
from nltk.corpus import stopwords

import matplotlib.pyplot as plt
import seaborn as sns
% matplotlib inline

# Input data files are available in the "../input/" directory.
from subprocess import check_output
# print(check_output(["ls", "../Final_Project/Data"]).decode("utf8"))
# Any results you write to the current directory are saved as output.

from sklearn.preprocessing import Imputer
from sklearn.feature_extraction.text import TfidfVectorizer

### 4.2. Process poster images to identify darkness and colorfulness of the overall image

The goal here is to represent darkness and colorfulness in a quantitative and consistent manner. The method we used here is both able to yield meaningful results and easy to implement:

- **Darkness**: we use the average of RGB values within the entire image as a first-order representation of overall darkness of an image
- **Colorfulness**: we first calculate the variance of R, G, and B respectively within the entire image, and then take an average of the 3 variances. This avoids accounting for the internal variability of R, G, and B of a single pixle.

In [34]:
# Load checkpoint
df4 = pd.read_csv("Data/data_cleaning_41.csv")

In [35]:
# Poster path from the dataframe
df4['poster_path'].head()

0    /rhIRbceoE9lR4veEXuwCC2wARtG.jpg
1    /vzmL6fP7aPKNKPRTFnZmiUfciyV.jpg
2    /6ksm1sjKMFLbO7UY2i6G1ju9SML.jpg
3    /16XOMpEaLWkrcPqSQqhTmeJuqQl.jpg
4    /e64sOI48hQXyru7naBFyssKFxVd.jpg
Name: poster_path, dtype: object

In [43]:
# Retrieve data from urls as a list of image data
base_url = "http://image.tmdb.org/t/p/w185_and_h278_bestv2"
i = 0
images = []

for poster in df4["poster_path"]:
    print("Image #: " + str(i))
    try:
        url = (base_url + poster)
        print("Grabbing image from: " + url)
        image = io.imread(url)
        images.append(image)
        i += 1
    except TypeError:
        print("Invalid URL")
        images.append(np.nan)        
        i+=1

Image #: 0
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/rhIRbceoE9lR4veEXuwCC2wARtG.jpg
Image #: 1
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/vzmL6fP7aPKNKPRTFnZmiUfciyV.jpg
Image #: 2
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/6ksm1sjKMFLbO7UY2i6G1ju9SML.jpg
Image #: 3
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/16XOMpEaLWkrcPqSQqhTmeJuqQl.jpg
Image #: 4
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/e64sOI48hQXyru7naBFyssKFxVd.jpg
Image #: 5
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/zMyfPUelumio3tiDKPffaUpsQTD.jpg
Image #: 6
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/jQh15y5YB7bWz1NtffNZmRw0s9D.jpg
Image #: 7
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/sGO5Qa55p7wTu7FJcX4H4xIVKvS.jpg
Image #: 8
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/eoWvKD60lT95Ss1MYNgVExpo5iU.jpg
I

Image #: 76
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tuIDKBp92R4tGFOB46MofvakfiY.jpg
Image #: 77
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/mMXL84GqES2HYpJ0Zt18I7m6mfU.jpg
Image #: 78
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/7aXOB0DyZPxNOYbaQ2oiNn64jm3.jpg
Image #: 79
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/96UDOJNgJXHmQMJqA79bKS9PR8i.jpg
Image #: 80
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/ysKIolKO0376Nl5DV1fDAAPudEq.jpg
Image #: 81
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bIQp2SJrVXiQttv9hXeqliQox0K.jpg
Image #: 82
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tsJSlkFSZPQhhVuKrYJXNClYaPD.jpg
Image #: 83
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/pfgpkDNcwSi1x4jVzeLqvxTwX5a.jpg
Image #: 84
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1QyCF6IFoX5WJIYHOkmLa3vz

Image #: 152
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/5CQgpLITPo33AEN1jULsyiHxSDJ.jpg
Image #: 153
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/qa9yf3OlfXbYBb0af0mpawGB6TI.jpg
Image #: 154
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/qnKARYBofUzHkBY8x9GWSNSoota.jpg
Image #: 155
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/cpMbvFDD2C21pqMNXVPhSWGQBR9.jpg
Image #: 156
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/ugGhvQoGBrefqmkeBvBgT4YVCRk.jpg
Image #: 157
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wjeQaiAApgzdipkNXhQnBrqjBY9.jpg
Image #: 158
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/oDJyDX11HW4j565vUjmFagKxDTQ.jpg
Image #: 159
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yzK39sdkGoiSyKZEWT6HQzaC0BX.jpg
Image #: 160
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/7eVo5DbP7gcsDzH

Image #: 226
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/3PEAkZHa8ehfUkuKbzmQNRTTAAs.jpg
Image #: 227
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/jGjSu9zlR2I8t6OE54uxSJ7M25p.jpg
Image #: 228
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/oIwrh7QhwUNxejsvgKtFG4V0gaQ.jpg
Image #: 229
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/9oIEKFVPhgVEzbcbRPDXCdkUgRN.jpg
Image #: 230
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/9qBe2sUDyY2dFH1iHq0SZb1G4QG.jpg
Image #: 231
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bZqvonwVru1XtnniQZgZRa3Znyk.jpg
Image #: 232
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/l8lq77bNqJY94JCMPI731jwtDsE.jpg
Image #: 233
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/oDufYQrDhdAsJlwQUnjY9wHRWgL.jpg
Image #: 234
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bycmMhO3iIoEDzP

Image #: 299
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/hvHNlMvWS2GBt7RR971bJ3k4bJc.jpg
Image #: 300
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/jP8ONbgwpQm5ojrtFuKCwvG1wCs.jpg
Image #: 301
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/77CFEssoKesi4zvtADEpIrSKhA3.jpg
Image #: 302
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/ztIqf7yGmb4JRFiv2i62K6PhTQR.jpg
Image #: 303
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/xOLY69rXKwuH9JUnOE4G2HHKiW5.jpg
Image #: 304
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/gM516lPBoHPYjgrLrmZKoNfNm6X.jpg
Image #: 305
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bIxNdNo4jNBLpcUoWvQ7LEnuA0w.jpg
Image #: 306
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/l9mzb7eJ1SOLEwcmLHBa27YtiXR.jpg
Image #: 307
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/9EwB291UkaAHhS3

...

Image #: 17233
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/glFXjFSIhyPIPKsg86vqxo029oM.jpg
Image #: 17234
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/glFXjFSIhyPIPKsg86vqxo029oM.jpg
Image #: 17235
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/mu3QtBZvVEwcgMnv6F6ujJcfE2a.jpg
Image #: 17236
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/ww8S5wCdjcxotux6Xvz4pxynrPA.jpg
Image #: 17237
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1FgWYqjfPEfwuvwrq1MTEclBJGa.jpg
Image #: 17238
Invalid URL
Image #: 17239
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bNofq5QmwFeFTILeUOzwG9hPe1X.jpg
Image #: 17240
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/8MnWBN1VsyvZsjodAxuAUPp3KYw.jpg
Image #: 17241
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wDkzrSoP8XWeEPYNR2J1SiEZIJz.jpg
Image #: 17242
Invalid URL
Image #: 17243
Invalid URL

Image #: 17309
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/ixd6fu6rhXg3pZBiD9ocbnXETUK.jpg
Image #: 17310
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/aI73Uy6NLAj7TdJHyMEA4Lhqcix.jpg
Image #: 17311
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/9uyC3ERRpGNkpqRNVgfEgZwOlJ8.jpg
Image #: 17312
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/xSlU3hHz7uFGV7JMA5lL0yaJivT.jpg
Image #: 17313
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/acJs6zfJoByFnMkNI8kjt3FCOh3.jpg
Image #: 17314
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1BMCqRxfR5Rjpo1kLqC02OF3h4Z.jpg
Image #: 17315
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/dyh7o8alcsQ3RVC9mDAbuxVjxo1.jpg
Image #: 17316
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/geX5Lg2TK6KUvbRl0D2YV1rUpgG.jpg
Image #: 17317
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 17385
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yCwQrknm1xM026EtjkFiyWJA9m1.jpg
Image #: 17386
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/txlf3B8eCkXD3xgJ5R8rUQRvbIk.jpg
Image #: 17387
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bnEgt5hk7WqrdMfGo3lkobTHoNf.jpg
Image #: 17388
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/vT3hvAk6cXVhQBP3VKWDcKonP3u.jpg
Image #: 17389
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/fFZqGnZ0Uoo9uE5f66GytmOVZGC.jpg
Image #: 17390
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/nFxEd9bEWoFk3MQoNRD0nxxLI7a.jpg
Image #: 17391
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/gZYTYK5FVmf7kaGqziaSGNOnTdV.jpg
Image #: 17392
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/uEWVI9xHRW1ffWV7AZO7zaKdn01.jpg
Image #: 17393
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 17459
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/uVl1ONS5b33QA8dVtvSmgWptIJM.jpg
Image #: 17460
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/8SnnBM4jk5uYsfM4X1vz2p18QL5.jpg
Image #: 17461
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/dINoFZOn1Js6SdNVjIcth1420t6.jpg
Image #: 17462
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/s1c1lq12iTjtKS3ucHr0tCvLIZq.jpg
Image #: 17463
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4xgoXt10glBXNnNblGmVFqwhysB.jpg
Image #: 17464
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/edyDny22vVgylMF9Xt0PFpolPOW.jpg
Image #: 17465
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/r4tkg6m5ExAE0asyke3oWO6GCsB.jpg
Image #: 17466
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/w7zHjPKrfl6HyATMY9r9uAkoLU2.jpg
Image #: 17467
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

KeyboardInterrupt: 

In [54]:
# Resume from Image #: 17469
for poster in df4["poster_path"][len(images):]:
    print("Image #: " + str(i))
    try:
        url = (base_url + poster)
        print("Grabbing image from: " + url)
        image = io.imread(url)
        images.append(image)
        i += 1
    except TypeError:
        print("Invalid URL")
        images.append(np.nan)        
        i+=1

Image #: 17469
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/utsYe7NaVdiUhXpBwgln3LTucYs.jpg
Image #: 17470
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/cyD6dWy4paQuKesOsIIA8NYkwUJ.jpg
Image #: 17471
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yppy37DEChYfV6LLtTwkAPAt3bE.jpg
Image #: 17472
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4iXyUfV6GjTl2C5o0D0osw935uQ.jpg
Image #: 17473
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/55Pc2K1cSEMh8UgUJONU7hqUPBk.jpg
Image #: 17474
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/nxBK6qjkDKTMFhqZcQSUo2FEHcE.jpg
Image #: 17475
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/croUg2bSjSMZwFgrTBv3FauRc6b.jpg
Image #: 17476
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/5SWjiawtjujD9926peDZmI6lThA.jpg
Image #: 17477
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 17542
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/eHldUGDNxb4ZPQSPDnGolyFDECa.jpg
Image #: 17543
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/s3YLp5qaWYmLnW3bh6046foiyYj.jpg
Image #: 17544
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/megksvf8JNB4gNCPn67w6kDz5zH.jpg
Image #: 17545
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/aoxgzp1QLDHnR2GgXB56F6HkX19.jpg
Image #: 17546
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4RgTIUbXRPNlbNgfAfHBrpptZmg.jpg
Image #: 17547
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1iHSVb8sKAfAJLY1aCdNUf3MPrx.jpg
Image #: 17548
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tvzhYJES47MQnG39KIXDhRa6BGj.jpg
Image #: 17549
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/oRx2omU5brPBjjYr0AZGCvN0F55.jpg
Image #: 17550
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 17615
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/lkmEyiGKQLfaym7lfKPdKjk3kwe.jpg
Image #: 17616
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/zM9IT7IeUJ2pY42vx8OhUgklVMu.jpg
Image #: 17617
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/rDtuKHcvg6QnTRWc25sXnojPNZH.jpg
Image #: 17618
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/vLatzdGxczcS9CCil6gmOyfe1Tm.jpg
Image #: 17619
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/6w4pIJtjNYyiXqtakjth3iDxhJE.jpg
Image #: 17620
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/c0leAM2XsHNG4U8jitGkaKBQs55.jpg
Image #: 17621
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1h6SRfYCykiX6iHMzRatl6iXCRt.jpg
Image #: 17622
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/h43jPTebYOabSXqNQqrRQpg6DPc.jpg
Image #: 17623
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 17687
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/dJVkWNpuLYG0ogZesOPMeHN2M7k.jpg
Image #: 17688
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4V6AD5rGZ8yA2f6gBocSgXOW3j5.jpg
Image #: 17689
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/3wOi7xgVbGBrMUyJRVe0CY3L010.jpg
Image #: 17690
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/q2OgXF4pJ668m4y4h4wNTpguX6H.jpg
Image #: 17691
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/vgRPlYHiottQpDav3nfw9Q1zAJJ.jpg
Image #: 17692
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tKXAcQ4CgqtKJg1uXevVxXAFLJe.jpg
Image #: 17693
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/3gWkOByTuAlsRgcBYNSLgjSEhVy.jpg
Image #: 17694
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/2KZO9nvSFpOdR35uNFUw9mc0RIR.jpg
Image #: 17695
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 17762
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/h1SofmVuZXYrr8o0GtxQoKCYspe.jpg
Image #: 17763
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/devLzCOnSjKKXNZmXxVB8Rd86bA.jpg
Image #: 17764
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yUgEmG1KHsI97FKtYwHTZP8znrD.jpg
Image #: 17765
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/oYhYHGcvDbSCIxKdREiYnkoxT9B.jpg
Image #: 17766
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/vgNm2IpecDj2qZD5tsTTfIJtXrb.jpg
Image #: 17767
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/jZdTCkgNdf7JYkFG3TIYcpWXAll.jpg
Image #: 17768
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/sTt5EjrryCkM3jvU7a5nqBKt0FB.jpg
Image #: 17769
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/abqsRCiSEEzNguLXdF7Kf7MKJGP.jpg
Image #: 17770
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

...

Image #: 32886
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/fqFSU3hdRQKsPxJ3OYh3nyVZqY1.jpg
Image #: 32887
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wR7sEPbgKKbpA6H1OdTWnkD4Jhc.jpg
Image #: 32888
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1g2uNpyCnbw4z21Y3z6ALBGd5sC.jpg
Image #: 32889
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/2SdF6BDdOwOfoBPsXMGytEv0cle.jpg
Image #: 32890
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/di8E99xJnQa9MGpnoC1oeZbZyCX.jpg
Image #: 32891
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/5GVPBrzJSusXuJfUdj106LuZKKM.jpg
Image #: 32892
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/6uSHYTVU0i2cLIgJGsV2FEyILkC.jpg
Image #: 32893
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/gwIvyScYFO44JmiM5ce3Tv1ESrJ.jpg
Image #: 32894
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 32959
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/cwj0Jn5Jo10PWYhaaJ1N5Y1j7lv.jpg
Image #: 32960
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/iOojYzI7WjN9ypyhX3fc0jm2hSD.jpg
Image #: 32961
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1B5t4UX63Qy1F0cqlexxCxKw9TJ.jpg
Image #: 32962
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tnvMbATIWDIapI8fnldrs8GU311.jpg
Image #: 32963
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/fw06Z3k24j9gYaOqCj9iMGrYEEt.jpg
Image #: 32964
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/sh3ZzwevODVVdHzHq3XPDvvgJUI.jpg
Image #: 32965
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/cFQHMUmxaO3PEDo5lxuQC8MCRIH.jpg
Image #: 32966
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/iyqwK3UU1KHR9Ey5tw5amRhSRXJ.jpg
Image #: 32967
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 33033
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/gPQfUcXOfhTTUR3mhByuDfQEUWS.jpg
Image #: 33034
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/7IsAiE4hXV7YOn7jDfdna6a6v7E.jpg
Image #: 33035
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/6VsHLBuVaTKXSYHqdCCgZWIYvrp.jpg
Image #: 33036
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/xZF4k6BJlKcBxoZSGZVWeAMT4qV.jpg
Image #: 33037
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wOtfvmZWjXHmVPNABNoR4g8C8kq.jpg
Image #: 33038
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/uznb3nUaOMtKWlvy2mKeZkDkfdj.jpg
Image #: 33039
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/vctzmTinuLACl2PIFuPhTNkTc62.jpg
Image #: 33040
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/518NatjyNRIUcFT2rxduNOl1tWQ.jpg
Image #: 33041
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 33108
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bW60uES0XoUZI4YQQP2AZ7d6v2o.jpg
Image #: 33109
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/3Oh9WELA95bAdww64Ml4Qe09aVD.jpg
Image #: 33110
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/g8McNXXv2vJD5qqgqhhe02PScfL.jpg
Image #: 33111
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bfB9Om15x6wQLfvRoEBz2KMxQ5r.jpg
Image #: 33112
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/rMbWbX2vEQPizm3VALUFmBN4KKa.jpg
Image #: 33113
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yv1QSfAy4PcpqNts419PfMZmxpo.jpg
Image #: 33114
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4VWHuNg8FphNyPIBKEia0M1kj5N.jpg
Image #: 33115
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/hpPA6Ln2mINqLsgJA1PABYtJpX2.jpg
Image #: 33116
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

ConnectionResetError: [Errno 54] Connection reset by peer

In [56]:
# Resume from Image #: 33131
for poster in df4["poster_path"][len(images):]:
    print("Image #: " + str(i))
    try:
        url = (base_url + poster)
        print("Grabbing image from: " + url)
        image = io.imread(url)
        images.append(image)
        i += 1
    except TypeError:
        print("Invalid URL")
        images.append(np.nan)        
        i+=1

Image #: 33131
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/szOB6uJe3W8G671KNnMWFXQOZwV.jpg
Image #: 33132
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/15N7MDXpxpmALJpfjKZ23vAguSd.jpg
Image #: 33133
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/eVt3M4BcwKx6MrdSGY9CVU8gWtH.jpg
Image #: 33134
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/rNbt3n790eZlhEnf47xubg5cyPw.jpg
Image #: 33135
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yNn4diwZxukfcgIGwpkDeqTwRsn.jpg
Image #: 33136
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/6GAnKeeKMXh8gm5Zudydd3TnBjC.jpg
Image #: 33137
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wtzggVjmtzeI508ktEejEAqofLu.jpg
Image #: 33138
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yONyhOUSaAMO3dyxTd3NqeBEXDp.jpg
Image #: 33139
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 33203
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/g2xZQZEmUP2TOylXq1UDT5SFSwo.jpg
Image #: 33204
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/irPlf6ay7hjQVER7R7gE1dkspkq.jpg
Image #: 33205
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/uPee6Nq6IxIOnG9KYnY5kxZP2cw.jpg
Image #: 33206
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/oOymJmOKBE9YlOmGVdPEpnNgeYx.jpg
Image #: 33207
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/lcBEjbd5XfnMaqIBpRoxOmYGqHe.jpg
Image #: 33208
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/6cPLskkOlnpfsWuJnp1a5twcIQL.jpg
Image #: 33209
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tcT7iuSRPFteCYbusbXJBdrEsfW.jpg
Image #: 33210
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/mxrNK5TtBDtxD7C7s8viN9xahz7.jpg
Image #: 33211
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 33278
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bURwPl3zBfYkHnlPu7iCLcEmUJi.jpg
Image #: 33279
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/iX8hyPXbkcUCnwqdiPeG3o1ECht.jpg
Image #: 33280
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/jjBthOisXwuyUqBd1BAmIzdSf4S.jpg
Image #: 33281
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/aj91KU7lZNrx7NtobMnib5QMC0x.jpg
Image #: 33282
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/fobk2sPDwnXI7l0MxBJfanAwSyT.jpg
Image #: 33283
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/yMwDt1q6YGodXyLTJeLhIpAsIKD.jpg
Image #: 33284
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/6vgWwpd9afTDtOoqjXvsprk3P0p.jpg
Image #: 33285
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/frC8bz4AtpfQjVuB7UYFoLw21m1.jpg
Image #: 33286
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 33353
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/9A28DXRMYMVfNkUc6Iof9Gov12K.jpg
Image #: 33354
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4SO94KNRWGR9jZNEoPotJUBNV3O.jpg
Image #: 33355
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/1UH35HH7TgB2nh9MBDSWAWoXWPk.jpg
Image #: 33356
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/s2Roj8ZnGOvWBKBEs1NMZvtP3Vs.jpg
Image #: 33357
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/UZQiLlZsU47yC64iEwIwdEHjGN.jpg
Image #: 33358
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/9kArqpBC9W3ga8FVJnLYKKActS4.jpg
Image #: 33359
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/uTowAuywfFKCtaOxoK9MHbyvAMh.jpg
Image #: 33360
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/dednQp2uIbmsPPbgtOixlgGfVzL.jpg
Image #: 33361
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv

Image #: 33425
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/bGBChmdEJ10OcrUq6SSZ8DFFSTo.jpg
Image #: 33426
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/hSVbQgmeo9PjyRZnDHUmDxQIWFB.jpg
Image #: 33427
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/mf9N89fyQt2BjWxVhixfB8iqOq1.jpg
Image #: 33428
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/lpfiGuO7R0VUMNORGjRWsOEZiXQ.jpg
Image #: 33429
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/akobRyRa3AH6Ze1120jdORJYRPY.jpg
Image #: 33430
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4zxhlPQa4c6Fs5CDcwh9AWRUGHa.jpg
Image #: 33431
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/70KYVhtYRDomBNM5hf0r2CezOy5.jpg
Image #: 33432
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tz9iX1hXzHubhBf25yqxoZm4tHi.jpg
Image #: 33433
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

...

Image #: 44681
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/r1hp0txnRXhUVCyC52RiTZ0yGNx.jpg
Image #: 44682
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/lrN3SddyHAOCHZyN7vYz9wLP47H.jpg
Image #: 44683
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/b62qKY2ffvO0z2LCSQRnXlUVC6I.jpg
Image #: 44684
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/iLbEUgK05CYSkyI4AHqOOAMxnam.jpg
Image #: 44685
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wfJoGeTOfU1ZY7hUJCY5DKEZ8G0.jpg
Image #: 44686
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/rWinmi3NrbUKc05TAS6bI1pqghF.jpg
Image #: 44687
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/8NTUkoL04Mo8rvFrXAWUAZLerTN.jpg
Image #: 44688
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/jgja6DiiT2LDq1Dnq2hWMPPBkKT.jpg
Image #: 44689
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 44753
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/rZ61OQW9xnal6MRIPILTvQNQUGf.jpg
Image #: 44754
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/4MCWcbDC9nGNY30y4Jy4B5WUAXb.jpg
Image #: 44755
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/b9tECZJXzPTCepGulfuA5uGEuIo.jpg
Image #: 44756
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/miBb3nqT5F0ruLtZeHLV9pf9363.jpg
Image #: 44757
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tPkgBEpq1Rx7wcTFEjZFRhbTLrd.jpg
Image #: 44758
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/aCADpnzne3ByjAXhwmqDfgkANve.jpg
Image #: 44759
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/turUYgFnjfsjPssIeWSLiNJFIla.jpg
Image #: 44760
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/fcpCBc2cDaeP23POjT44NnZZAkp.jpg
Image #: 44761
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 44829
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/aqsOVgnyluaNBshe50r013hI9hl.jpg
Image #: 44830
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wmQuRPCBVGiRCsj93C3KEZC0qB7.jpg
Image #: 44831
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/tee3vtIWFQhsKvKJmGtdw2E5eXn.jpg
Image #: 44832
Invalid URL
Image #: 44833
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/hP1zVEGyTsAvxwaUC7rVgJdIS0O.jpg
Image #: 44834
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/ogZyHLeupTifSq9ae4WaO9e0ynO.jpg
Image #: 44835
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/zsX5DD8CNACt0QGRTCm8XEIQsLi.jpg
Image #: 44836
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/uJa46AUopgJx4y8Qr5QOL78BqRA.jpg
Image #: 44837
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/g6OG2MkBNGfEM7r5D9JGvHTWvDA.jpg
Image #: 44838
Grabbing image from: http://image.tmdb

Image #: 44905
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/xShOZM3yHD00MOJKBegQ0o8RTvD.jpg
Image #: 44906
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/wB5f6gOiqHR8lJWxjIlBJnLbF0s.jpg
Image #: 44907
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/mF7L0KIt3i8L5vpN2uLhyNlcvyM.jpg
Image #: 44908
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/gTLYkTZWLo5NkWGdMbSHiCLo3aa.jpg
Image #: 44909
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/kObIQERttnMmGNhYKj0sPRVTdXc.jpg
Image #: 44910
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/fT3i5Yegn1gqoNsfV1utk1vwcvU.jpg
Image #: 44911
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/c4v2ng9xfwt5dEP5T6ngeimozLu.jpg
Image #: 44912
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/36KPcZJbbZKqvfeWjyG5xcHYHKR.jpg
Image #: 44913
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_best

Image #: 44981
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/d5bX92nDsISNhu3ZT69uHwmfCGw.jpg
Image #: 44982
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/aorBPO7ak8e8iJKT5OcqYxU3jlK.jpg
Image #: 44983
Grabbing image from: http://image.tmdb.org/t/p/w185_and_h278_bestv2/s5UkZt6NTsrS7ZF0Rh8nzupRlIU.jpg


In [ ]:
# # Save list of images
# np.save('Data/images.npy', images)

# # Load list of images
# images = np.load("Data/images.npy")

In [57]:
# Sanity check
print(f"Shape of dataframe's poster column: {df4['poster_path'].shape}")
print(f"Length of the list: {len(images)}")
print(f"Shape of each image: {images[0].shape}")

Shape of dataframe's poster column: (44984,)
Length of the list: 44984
Shape of each image: (278, 185, 3)


In [71]:
# Calculate variance and mean of each image
variances = []
means = []

for image in images:
    try:
        variances.append(np.mean(np.var(image, axis=(0,1))))
        means.append(np.mean(image))
    except:
        variances.append(np.nan)
        means.append(np.nan)


In [75]:
# Add darkness and colorfulness columns to the dataframe
se_dark = pd.Series(means)
se_color = pd.Series(variances)
df4['darkness'] = se_dark.values
df4['colorfulness'] = se_color.values

# Drop the original poster path colomn because it's no longer useful
df4 = df4.drop(columns=['poster_path'])

# Save as a checkpoint
df4.to_csv("Data/data_cleaning_42.csv", index=False)
df4.to_csv("Data/data_cleaning_42.csv.gz",index=False,compression="gzip")

In [77]:
df4.head()

adult  belongs_to_collection      budget  \
0  False                      1  30000000.0   
1  False                      0  65000000.0   
2  False                      1   8000000.0   
3  False                      0  16000000.0   
4  False                      1   8000000.0   

                               genres  homepage       id    imdb_id  \
0   ['Animation', 'Comedy', 'Family']         1    862.0  tt0114709   
1  ['Adventure', 'Fantasy', 'Family']         0   8844.0  tt0113497   
2               ['Romance', 'Comedy']         0  15602.0  tt0113228   
3      ['Comedy', 'Drama', 'Romance']         0  31357.0  tt0114885   
4                          ['Comedy']         0  11862.0  tt0113041   

  original_language               original_title  \
0                en                    Toy Story   
1                en                      Jumanji   
2                en             Grumpier Old Men   
3                en            Waiting to Exhale   
4                en  Father of the Bride Part II   

                                            overview      ...       \
0  Led by Woody, Andy's toys live happily in his ...      ...        
1  When siblings Judy and Peter discover an encha...      ...        
2  A family wedding reignites the ancient feud be...      ...        
3  Cheated on, mistreated and stepped on, the wom...      ...        
4  Just when George Banks has recovered from his ...      ...        

   vote_average vote_count                                               cast  \
0           7.7     5415.0          ['Tom Hanks', 'Tim Allen', 'Don Rickles']   
1           6.9     2413.0  ['Robin Williams', 'Jonathan Hyde', 'Kirsten D...   
2           6.5       92.0   ['Walter Matthau', 'Jack Lemmon', 'Ann-Margret']   
3           6.1       34.0  ['Whitney Houston', 'Angela Bassett', 'Loretta...   
4           5.7      173.0   ['Steve Martin', 'Diane Keaton', 'Martin Short']   

                                            keywords  cast_size  crew_size  \
0  ['jealousy', 'toy', 'boy', 'friendship', 'frie...         13        106   
1  ['board game', 'disappearance', "based on chil...         26         16   
2  ['fishing', 'best friend', 'duringcreditssting...          7          4   
3  ['based on novel', 'interracial relationship',...         10         10   
4  ['baby', 'midlife crisis', 'confidence', 'agin...         12          7   

          director weighted_rating    darkness  colorfulness  
0    John Lasseter        7.684269  118.188424   5680.062732  
1     Joe Johnston        6.876419  135.582449   6434.488365  
2    Howard Deutch        6.158197  113.667736   7449.801543  
3  Forest Whitaker        5.674989  167.193013   6489.089161  
4    Charles Shyer        5.624637  113.413060   9883.229671  

[5 rows x 30 columns]